### GEFSv12 Data from AWS

#### Kathy Pegion (kathypegion.com)
CLIM 680 Climate Data Analysis

This notebook demontrates how to:
* download a single GEFSv12 re-forecast data file from AWS without an AWS account
* how to read it in using `xarray`
* how to make an animation of the data in time using `hvplot`

## Import statements

`boto3` and `botocore` are for AWS

We will need to install them in our environment.

1. In a separate COLA terminal window (not in Jupyter), activate your clim680 environment if it is not already active:

`conda activate clim680`

2. Install `boto3` and `botocore`

`conda install -c conda-forge boto3`
`conda install -c conda-forge botocore`

They are now installed in your `clim680` environment.  It is a good idea to keep track of what you installed by adding it to your `environment.yml` file, but it is not required.

In [1]:
import boto3

from botocore import UNSIGNED
from botocore.client import Config

import matplotlib.pyplot as plt
import os.path
import xarray as xr
import cartopy

import hvplot.xarray

Data on AWS is located in specific locations called `buckets`, so we must specify the bucket we want to look in. 

The prefix is the list of subdirectories in that `bucket`

We got this information from looking through the data on the web interface to find the file we wanted. 

In [2]:
BUCKET = 'noaa-gefs-retrospective'
prefix = 'GEFSv12/reforecast/2000/2000010500/c00/Days:1-10/'

### Define filenames for the file the we want to download

In [3]:
varname='pres_msl'

remote_file=prefix+varname+'_2000010500_c00.grib2'
local_fname=os.path.basename(remote_file)
local_file='/scratch/kpegion/'+local_fname

print(local_file)
print(remote_file)

/scratch/kpegion/pres_msl_2000010500_c00.grib2
GEFSv12/reforecast/2000/2000010500/c00/Days:1-10/pres_msl_2000010500_c00.grib2


### Access AWS without having an account 
This will only allow access to open, public data.

In [4]:
s3 = boto3.resource(
    's3',
    aws_access_key_id='',
    aws_secret_access_key='',
    config=Config(signature_version=UNSIGNED)
)

### Download the file from AWS

Without an AWS account we can only download the data, we cannot
do any calculations with the data. 

In [5]:
s3.Bucket(BUCKET).download_file(remote_file, local_file)

### Read in downloaded file

In [6]:
ds=xr.open_dataset(local_file,engine='cfgrib',
                   backend_kwargs={'indexpath': ''})
ds

<xarray.Dataset>
Dimensions:     (latitude: 721, longitude: 1440, step: 80)
Coordinates:
    number      int64 ...
    time        datetime64[ns] ...
  * step        (step) timedelta64[ns] 0 days 03:00:00 ... 10 days 00:00:00
    meanSea     int64 ...
  * latitude    (latitude) float64 90.0 89.75 89.5 89.25 ... -89.5 -89.75 -90.0
  * longitude   (longitude) float64 0.0 0.25 0.5 0.75 ... 359.2 359.5 359.8
    valid_time  (step) datetime64[ns] ...
Data variables:
    msl         (step, latitude, longitude) float32 ...
Attributes:
    GRIB_edition:            2
    GRIB_centre:             kwbc
    GRIB_centreDescription:  US National Weather Service - NCEP 
    GRIB_subCentre:          2
    Conventions:             CF-1.7
    institution:             US National Weather Service - NCEP 
    history:                 2020-10-09T18:16:28 GRIB to CDM+CF via cfgrib-0....

### Convert from Pa to hPa

In [7]:
ds['msl']=ds['msl']/100.0

### Make animation using `hvplot`

In [8]:
ds['msl'].plot.contourf(groupby='step', 
                 widget_location='bottom',
                 geo=True,coastline=True,
                 cmap='RdBu_r',
                 label='Mean Sea Level Pressure (hPa)')

Column
    [0] HoloViews(DynamicMap, widget_location='bottom')
    [1] Row
        [0] HSpacer()
        [1] WidgetBox
            [0] DiscreteSlider(margin=(20, 20, 20, 20), name='time since forecast_refer..., options=OrderedDict([('10800000000...]), value=numpy.timedelta64(10800000..., width=250)
        [2] HSpacer()